In [4]:
import pandas as pd
import glob
from pandasql import sqldf
import pandas as pd
import numpy as np
import csv
import seaborn as sns
import re
import datetime as dt
from datetime import datetime
import pandas as pd
import pygwalker as pyg

pysqldf = lambda q: sqldf(q, globals())

In [5]:
#Maxing view
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [ ]:
#Resetting view
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')

In [6]:
df = pd.read_csv("food_data.csv", encoding = 'latin1')
df.columns = df.columns.str.replace(' ', '_')
#df.fillna('', inplace=True)
df

Date_of_fail                                Product_description  \
0      2019-01-11                             Frozen chopped spinach   
1      2019-05-16                  Frozen cooked vannamei prawn meat   
2      2019-05-31                      Pilchards in hot chilli sauce   
3      2019-06-03                           Dried seedless red dates   
4      2019-06-04                                Frozen dried longan   
5      2019-06-05                                  Mung chilka split   
6      2019-06-05                                          Mung dhal   
7      2019-06-05                             Kashmiri chilli powder   
8      2019-06-06                                      Cassava chips   
9      2019-06-06                                     Confectionery    
10     2019-06-07                    Frozen seasoned flying fish roe   
11     2019-06-11                                       Fresh lychee   
12     2019-06-11                                       Fresh lychee   
13     2019-06-11                               Frozen cooked prawns   
14     2019-06-12                                       Tea biscuits   
15     2019-06-12                                  Indian flat beans   
16     2019-06-13                                   Chocolate halawa   
17     2019-06-13                                       Green chilli   
18     2019-06-13                                         Red chilli   
19     2019-06-13                                Dried fish keeramin   
20     2019-06-14                                       Marinara mix   
21     2019-06-17                                        Kelp sheets   
22     2019-06-17                                Masala curry powder   
23     2019-06-17                      Frozen cooked vannamei prawns   
24     2019-06-17                                         Kelp knots   
25     2019-06-19                                       Fresh chilli   
26     2019-06-24                                      Tapioca chips   
27     2019-06-24            Nut crackers spicy coated fried peanuts   
28     2019-06-25                             Kashmiri chilli powder   
29     2019-06-25                                     Frozen cowpeas   
30     2019-06-25                             Kashmiri chilli powder   
31     2019-06-26                                      Wheaten flour   
32     2019-06-27                                     Tahini halawah   
33     2019-06-27                                     Tahini halawah   
34     2019-06-28                                 Cut hyacinth beans   
35     2019-07-01                                       Dried longan   
36     2019-07-02                       Dried fish tuyo in olive oil   
37     2019-07-02                                  Indian flat beans   
38     2019-07-03                                      Tapioca chips   
39     2019-07-03                                       Tea biscuits   
40     2019-07-04                                              Chips   
41     2019-07-04                       Pasteurised cooked crab meat   
42     2019-07-04                                Pata de mulo cheese   
43     2019-07-05                                  Ground dried fish   
44     2019-07-08                                      Fresh lychees   
45     2019-07-08                                        Mangosteens   
46     2019-07-08                                      Cassava chips   
47     2019-07-08                                        Wheat flour   
48     2019-07-08                                      Fresh lychees   
49     2019-07-09                                   Split mung beans   
50     2019-07-09                                      Tapioca chips   
51     2019-07-09                                    Roasted peanuts   
52     2019-07-09                                  High gluten flour   
53     2019-07-09                               Spiced fried peanuts   
54     2019-07-10                      Formul

In [7]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1546 entries, 0 to 1545
Data columns (total 11 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   Date_of_fail          1529 non-null   object
 1   Product_description   1530 non-null   object
 2   Country_of_origin     1529 non-null   object
 3   Producer_name         1527 non-null   object
 4   Reason_for_fail       1543 non-null   object
 5   Results               1391 non-null   object
 6   Units                 1105 non-null   object
 7   Reference             1532 non-null   object
 8   Category              1546 non-null   object
 9   Test_applied          468 non-null    object
 10  Holding_order_number  227 non-null    object
dtypes: object(11)
memory usage: 133.0+ KB


# Cleaning Product description

In [8]:
df.shape

(1546, 11)

In [9]:
def basic_clean(df,column):
    df[column] = df[column].str.replace('  ', ' ', regex=True)
    df[column] = df[column].apply(lambda x: re.sub(r'[^a-zA-Z0-9\s]+', '', str(x)))
    df[column] = df[column].str.strip()
    df[column] = df[column].str.lower()
    return df

In [10]:
for i in df.columns:
    if i == "Results" or i == "Date_of_fail" or i == "Units":
        continue
    elif i == "Producer_name":
        df = basic_clean(df,i)
        remove_words = ['pty', 'usa', 'ltd', 'pvt', 'co', 'sdn', 'bhd', 'inc',
                       'limited', 'china', 'india', 'korea', 'thailand', 'food'
                       'foods', 'corporation']
        df[i] = df[i].str.replace('  ', ' ', regex=True)
        pat = r'\b(?:{})\b'.format('|'.join(remove_words))
        df[i] = df[i].str.replace(pat, '', regex=True)
        df[i] = df[i].str.strip()
    elif i == "Country_of_origin":
        df = basic_clean(df,i)
        mapping = {'korea republic of': 'korea', 'republic of korea': 'korea',
                   'iran islamic republic of': 'iran', 'united states of america':'united states'}
        df[i] = df[i].replace(mapping)
    elif i == "Holding_order_number":
        df = basic_clean(df,i)
        df[i] = df[i].apply(lambda x: re.sub('[^0-9]+', '', str(x)))
    else:
        df = basic_clean(df,i)
df

Date_of_fail                                Product_description  \
0      2019-01-11                             frozen chopped spinach   
1      2019-05-16                  frozen cooked vannamei prawn meat   
2      2019-05-31                      pilchards in hot chilli sauce   
3      2019-06-03                           dried seedless red dates   
4      2019-06-04                                frozen dried longan   
5      2019-06-05                                  mung chilka split   
6      2019-06-05                                          mung dhal   
7      2019-06-05                             kashmiri chilli powder   
8      2019-06-06                                      cassava chips   
9      2019-06-06                                      confectionery   
10     2019-06-07                    frozen seasoned flying fish roe   
11     2019-06-11                                       fresh lychee   
12     2019-06-11                                       fresh lychee   
13     2019-06-11                               frozen cooked prawns   
14     2019-06-12                                       tea biscuits   
15     2019-06-12                                  indian flat beans   
16     2019-06-13                                   chocolate halawa   
17     2019-06-13                                       green chilli   
18     2019-06-13                                         red chilli   
19     2019-06-13                                dried fish keeramin   
20     2019-06-14                                       marinara mix   
21     2019-06-17                                        kelp sheets   
22     2019-06-17                                masala curry powder   
23     2019-06-17                      frozen cooked vannamei prawns   
24     2019-06-17                                         kelp knots   
25     2019-06-19                                       fresh chilli   
26     2019-06-24                                      tapioca chips   
27     2019-06-24            nut crackers spicy coated fried peanuts   
28     2019-06-25                             kashmiri chilli powder   
29     2019-06-25                                     frozen cowpeas   
30     2019-06-25                             kashmiri chilli powder   
31     2019-06-26                                      wheaten flour   
32     2019-06-27                                     tahini halawah   
33     2019-06-27                                     tahini halawah   
34     2019-06-28                                 cut hyacinth beans   
35     2019-07-01                                       dried longan   
36     2019-07-02                       dried fish tuyo in olive oil   
37     2019-07-02                                  indian flat beans   
38     2019-07-03                                      tapioca chips   
39     2019-07-03                                       tea biscuits   
40     2019-07-04                                              chips   
41     2019-07-04                       pasteurised cooked crab meat   
42     2019-07-04                                pata de mulo cheese   
43     2019-07-05                                  ground dried fish   
44     2019-07-08                                      fresh lychees   
45     2019-07-08                                        mangosteens   
46     2019-07-08                                      cassava chips   
47     2019-07-08                                        wheat flour   
48     2019-07-08                                      fresh lychees   
49     2019-07-09                                   split mung beans   
50     2019-07-09                                      tapioca chips   
51     2019-07-09                                    roasted peanuts   
52     2019-07-09                                  high gluten flour   
53     2019-07-09                               spiced fried peanuts   
54     2019-07-10                      formul

# Analysis (Univariate + Bivariate)

In [278]:
#Can't do much univariate + divariate analysis (categorical data + numbers are varied for different tests)

In [11]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1546 entries, 0 to 1545
Data columns (total 11 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   Date_of_fail          1529 non-null   object
 1   Product_description   1546 non-null   object
 2   Country_of_origin     1546 non-null   object
 3   Producer_name         1546 non-null   object
 4   Reason_for_fail       1546 non-null   object
 5   Results               1391 non-null   object
 6   Units                 1105 non-null   object
 7   Reference             1546 non-null   object
 8   Category              1546 non-null   object
 9   Test_applied          1546 non-null   object
 10  Holding_order_number  1546 non-null   object
dtypes: object(11)
memory usage: 133.0+ KB


# Analysis (pygwalker) (Really nice visual to check errors)

In [12]:
df.to_csv('food_data_cleaned.csv', index=False)
df = pd.read_csv('food_data_cleaned.csv', parse_dates=['Date_of_fail'])
gwalker = pyg.walk(df)